<a href="https://colab.research.google.com/github/MarlaS02/comp215/blob/main/labs/lab05_scaling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

COMP 215 - LAB 5
----------------
#### Name(s):
#### Date:

By the end of this lab you should be able to:
  * apply both a direct (ie. brute force) and heuristic algorithm to a problem
  * use the networkx module to visualize graphs
  * measure algorithm scaling


During this lab, you will be introduced to the following:
  * seeding the random module



## The Traveling Salesperson Problem

This lab is based on the famous Traveling Salesperson Problem (TSP) outlined in Section 3.3.2 of 'On Complexity'.  Imagine you needed to travel to ten different cities.  What is the sortest possible route you could take to visit every city?  For our version of the problem, you start from a specific city and must end on the same city.

In this lab, you will implement a direct (ie. brute force) and a heuristic solution to the problem.

In [1]:
# start with some imports
import random, math, time, itertools
import networkx as nx
import matplotlib.pyplot as plt
%matplotlib inline
from pprint import pprint

## Set up the map

For this implementation of the problem we will randomly place N cities on a 100 by 100 grid.  Cities will be labelled using a single character; 'A', 'B', 'C', etc.  City locations will be denoted by a 2-tuple, `(x,y)`, giving their position on the grid. In order to create reproducable maps, we will use [random.seed()](https://docs.python.org/3/library/random.html#random.seed) to initialize the random module.  

In [2]:
def setup_map(N, seed=1):
  ''' Returns a map of N cities with random locations on a 100 by 100 grid '''
  random.seed(seed)
  city_locations = [(random.randint(0, 100), random.randint(0, 100)) for i in range(N)]
  city_names = [chr(65 + i) for i in range(N)]
  city_map = dict(zip(city_names, city_locations))
  return city_map

def graph_map(city_map):
  ''' graph the map of cities using networkx'''
  G = nx.Graph()
  G.add_nodes_from(city_map)
  nx.draw(G, city_map, with_labels=True)

def distance(city1, city2, city_map):
  ''' Returns the distance between two cities on a map'''
  x1, y1 = city_map[city1]
  x2, y2 = city_map[city2]
  return round(math.sqrt((x2 - x1)**2 + (y2 - y1)**2),1)

def calculate_distances(city_map):
  ''' Returns a dictionary with the distances between all pairs of cities in a map '''
  distances = {}
  for city1 in city_map:
      for city2 in city_map:
          if city1 != city2:
              # this will have duplicate distances (A,B) and (B,A)
              # these duplicates make the algorithm implememntation simpler
              distances[(city1, city2)] = distance(city1, city2, city_map)
  return distances


In [3]:
# test our setup functions
city_map = setup_map(10)
print(f'City Map: {city_map}')
distances = calculate_distances(city_map)
print(f'Distances between cities: {distances}')
graph_map(city_map)
city_map_2 = setup_map(4)


City Map: {'A': (17, 72), 'B': (97, 8), 'C': (32, 15), 'D': (63, 97), 'E': (57, 60), 'F': (83, 48), 'G': (100, 26), 'H': (12, 62), 'I': (3, 49), 'J': (55, 77)}
Distances between cities: {('A', 'B'): 102.4, ('A', 'C'): 58.9, ('A', 'D'): 52.4, ('A', 'E'): 41.8, ('A', 'F'): 70.2, ('A', 'G'): 94.9, ('A', 'H'): 11.2, ('A', 'I'): 26.9, ('A', 'J'): 38.3, ('B', 'A'): 102.4, ('B', 'C'): 65.4, ('B', 'D'): 95.3, ('B', 'E'): 65.6, ('B', 'F'): 42.4, ('B', 'G'): 18.2, ('B', 'H'): 100.7, ('B', 'I'): 102.6, ('B', 'J'): 80.8, ('C', 'A'): 58.9, ('C', 'B'): 65.4, ('C', 'D'): 87.7, ('C', 'E'): 51.5, ('C', 'F'): 60.7, ('C', 'G'): 68.9, ('C', 'H'): 51.1, ('C', 'I'): 44.7, ('C', 'J'): 66.1, ('D', 'A'): 52.4, ('D', 'B'): 95.3, ('D', 'C'): 87.7, ('D', 'E'): 37.5, ('D', 'F'): 52.9, ('D', 'G'): 80.1, ('D', 'H'): 61.9, ('D', 'I'): 76.8, ('D', 'J'): 21.5, ('E', 'A'): 41.8, ('E', 'B'): 65.6, ('E', 'C'): 51.5, ('E', 'D'): 37.5, ('E', 'F'): 28.6, ('E', 'G'): 54.8, ('E', 'H'): 45.0, ('E', 'I'): 55.1, ('E', 'J'): 17.1,

### Exercise 1: The Brute Force Solution

Implement a brute force solution to the traveling salesman problem using the city map and distance dictionary given above.  The algorithm for the brute force solution looks something like this:
 1. Loop over every possible route that starts and ends on city A.  For a three city example, this would be ABCA, ACBA.  
 2. Calculate the total distance of each possible route.  
 3. Find the route with the minimum total distance.

Before you start coding, think about what functions and/or class you might want to simplify your implementation of the algorithm.  Write a small test for your algorithm.

In [8]:
# Ex. 1 your solution here

city_list = list(city_map.keys())
print(city_list)

city_list_2 = list(city_map_2.keys())

possible_routes = list(itertools.permutations(city_list[1:10]))
possible_routes_complete = [('A',) + char + ('A',) for char in possible_routes]
total_distances = []
for i in range(len(possible_routes_complete)):
  total_distance = 0
  for j in range(len(possible_routes_complete[i])-1):
    total_distance += distances[(possible_routes_complete[i][j], possible_routes_complete[i][j+1])]
  total_distances.append(total_distance)

assert len(possible_routes_complete) == 362880
assert len(total_distances) == 362880
print(total_distances)
print(min(total_distances))

possible_routes_2 = list(itertools.permutations(city_list_2[1:4]))
possible_routes_2_complete = [('A',) + char + ('A',) for char in possible_routes_2]
total_distances_2 = []
for i in range(len(possible_routes_2_complete)):
  total_distance_2 = 0
  for j in range(len(possible_routes_2_complete[i])-1):
    total_distance_2 += distances[(possible_routes_2_complete[i][j], possible_routes_2_complete[i][j+1])]
  total_distances_2.append(total_distance_2)

print(total_distances_2)
print(min(total_distances_2))

assert len(possible_routes_2_complete) == 6
assert len(total_distances_2) == 6

print(possible_routes_2_complete)

['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J']
[557.6999999999999, 576.0, 548.7, 564.9000000000001, 505.6, 503.50000000000006, 686.2, 643.1, 615.8, 631.8000000000001, 634.1, 693.2, 680.1999999999999, 626.0, 618.8, 625.8000000000001, 635.0000000000001, 696.2, 567.6999999999999, 556.6, 629.1, 617.8000000000001, 627.0000000000001, 626.8000000000001, 561.1999999999999, 579.5, 555.2, 571.4000000000001, 504.1, 502.00000000000006, 692.6999999999999, 641.5999999999999, 617.3, 628.3, 635.5999999999999, 697.7, 683.6999999999999, 624.5, 614.3, 619.3000000000001, 630.5, 694.7, 571.1999999999999, 563.1, 640.6, 627.3000000000001, 638.5000000000001, 633.3000000000001, 635.3, 592.1999999999999, 696.4, 712.4, 645.3000000000001, 704.4, 638.3000000000001, 587.2, 691.4, 702.4000000000001, 648.3, 710.4000000000001, 567.9, 637.0, 559.9, 632.0, 575.9000000000001, 578.9000000000001, 578.2, 698.4, 586.1999999999999, 701.4000000000001, 645.3, 640.3000000000001, 634.8, 580.6000000000001, 701.9, 708.9, 642.70

### Exercise 2: Nearest Neighbour

Implement a nearest neighbour solution to the traveling salesman problem using the city map and distance dictionary given above.  The algorithm for the nearest neighbour solution looks something like this:
 1. Start from the starting city.  
 2. Go to the nearest city that has not been visited.  
 3. Repeat steps 1 and 2 until all cities have been visited.

Before you start coding, think about what functions and/or class you might want to simplify your implementation of the algorithm.  Write a small test for your algorithm.

In [19]:
# Ex.2 your code here

current_city = 'A'
next_stop = ''
smallest_distance = 1000000
visited_cities = []

while len(visited_cities) < 10:

  for i in range(10):
    char_1 = chr(65 + i)
    if char_1 not in visited_cities and char_1 != current_city and distances[(current_city, char_1)] < smallest_distance:
       next_stop = char_1
       smallest_distance = distances[(current_city, char_1)]


  visited_cities.append(current_city)

  current_city = next_stop
  smallest_distance = 100000
  next_stop = ''

print(visited_cities)

['A', 'H', 'I', 'C', 'E', 'J', 'D', 'F', 'G', 'B']


### Exercise 3: Graph the Routes

Use the networkx module to create directed graphs of the routes (brute force and nearest neighbour).  Include the distances between the cities on the edges.  Run several different map setups with a different sizes (ie. number of cities).  Do the brute force (ie. direct) and nearest neighbour (ie. heuristic) algorithms always give the same solution?  Do you notice anything about the brute force solutions that suggests an alternative heuristic algorithm?


In [ ]:
# Ex.3 your code here

### Exercise 4: Algorithm Scaling

Use the `time` module to measure the running time of the two algorithms.  Note that the `time.time()` function returns the current time, so calling it before and after the algorithm has run can give you the time it takes for the algorithm to execute.  Taking the average over several trials will make the measurement more precise.  Demonstrate the scaling nature of the algorithms by plotting their execution time as a function of N, up to about N = 10.  

In [ ]:
# Ex 4: your code here